In [1]:
%load_ext autoreload

In [2]:
%autoreload 2
import json
import pickle
import pandas as pd
from glob import glob
from pathlib import Path
import scipy.sparse as sp
from pprint import pprint
from tqdm.notebook import tqdm
from gensim.models.word2vec import Word2Vec

import sys
sys.path.append('../../')

import src.test.util as test_util

# Imports

In [3]:
path_to_test_data = Path("../../data") / "test"
path_to_tppmi_model = Path("../../data") / "ppmi-matrices" / "nyt-data"
path_to_twec_model = Path("../../model") / "nyt-data" / "cade" / "model"
path_to_static_model = Path("../../model") / "nyt-data" / "static"

# Setup

## Testsets

### Testset 1

Based on publicly recorded knowledge that for each year lists different names for a particular role, such as U.S. president, U.K. prime minister, NFL superbowl champion team, and so on.

In [4]:
test_data = pd.read_csv(path_to_test_data / "testset_1.csv")
test_data.columns = ['truth', 'equivalent']
test_data = test_data.sort_values(by='truth', ascending=True)
test_cases = test_data['truth'].unique()

print("Testset")
print(f"Testcases (all): {len(test_data)}")
print(f"Testcases (unique): {len(test_cases)}")

Testset
Testcases (all): 11027
Testcases (unique): 499


Split testset into static and dynamic testcases

In [5]:
# Splitting the columns into words and years
split_truth = test_data['truth'].str.split('-', expand=True)
split_equivalent = test_data['equivalent'].str.split('-', expand=True)

# Creating masks for "static" and "dynamic" conditions
static_mask = split_truth[0] == split_equivalent[0]
dynamic_mask = split_truth[0] != split_equivalent[0]

# Applying the masks to create the separate DataFrames
test_data_static = test_data[static_mask]
test_data_dynamic = test_data[dynamic_mask]

test_cases_static = test_data_static['truth'].unique()
test_cases_dynamic = test_data_dynamic['truth'].unique()

In [6]:
print("Static")
print("------------------")
print(f"Testcases (all): {len(test_data_static)}")
print(f"Testcases (unique): {len(test_cases_static)}")
print("Dynamic")
print("------------------")
print(f"Testcases (all): {len(test_data_dynamic)}")
print(f"Testcases (unique): {len(test_cases_dynamic)}")

Static
------------------
Testcases (all): 2937
Testcases (unique): 443
Dynamic
------------------
Testcases (all): 8090
Testcases (unique): 499


In [7]:
print(len(test_cases))

499


## Models

### TWEC

In [8]:
model_filenames_cade = glob(str(path_to_twec_model / "*_data.model"))

In [9]:
# load models
models_cade = {f"model_{model_file.split('_data')[0][-4:]}":Word2Vec.load(model_file) for model_file in tqdm(model_filenames_cade)}

  0%|          | 0/27 [00:00<?, ?it/s]

In [10]:
models_cade = {model_key: models_cade[model_key] for model_key in sorted(models_cade, key=lambda x: int(x.split('_')[1]))}

In [11]:
models_cade.keys()

dict_keys(['model_1990', 'model_1991', 'model_1992', 'model_1993', 'model_1994', 'model_1995', 'model_1996', 'model_1997', 'model_1998', 'model_1999', 'model_2000', 'model_2001', 'model_2002', 'model_2003', 'model_2004', 'model_2005', 'model_2006', 'model_2007', 'model_2008', 'model_2009', 'model_2010', 'model_2011', 'model_2012', 'model_2013', 'model_2014', 'model_2015', 'model_2016'])

Create dictionary of testsets that contain all test-words along with their embedding in the respective year

In [12]:
test_case_dict_cade = test_util.create_test_case_dict_cade(test_cases, models_cade)

2 Testcases are not in the vocab of the model(s)


Retrieve most similar words for each testword in each year

In [13]:
similarities_cade = test_util.get_similarities_of_models(models_cade, test_case_dict_cade)

  0%|          | 0/497 [00:00<?, ?it/s]

In [14]:
similarities_cade

{'49ers-1990': {'1990': [('49ers', 1.0),
   ('rams', 0.9142225384712219),
   ('broncos', 0.8876343369483948),
   ('everett', 0.8765201568603516),
   ('oilers', 0.8624967932701111),
   ('giants', 0.8569235801696777),
   ('vikings', 0.8563781380653381),
   ('eagles', 0.8512576222419739),
   ('quarterback', 0.8509493470191956),
   ('redskins', 0.8468084335327148)],
  '1991': [('falcons', 0.895034909248352),
   ('redskins', 0.8870956301689148),
   ('giants', 0.8732050657272339),
   ('eagles', 0.8424596190452576),
   ('49ers', 0.8326606750488281),
   ('lions', 0.8275255560874939),
   ('quarterback', 0.8203926682472229),
   ('jets', 0.8197599053382874),
   ('quarterbacks', 0.8186768889427185),
   ('bears', 0.8118192553520203)],
  '1992': [('redskins', 0.9050107002258301),
   ('49ers', 0.883254885673523),
   ('falcons', 0.8808400630950928),
   ('quarterback', 0.87618488073349),
   ('vikings', 0.8712279796600342),
   ('bengals', 0.8646988868713379),
   ('broncos', 0.8578092455863953),
   ('oil

### Static Word2Vec

In [21]:
model_static = Word2Vec.load(str(path_to_static_model / "w2v_model.model"))

In [22]:
test_case_dict_static = test_util.create_test_case_dict_static(model_static, test_cases)

0 Testcases are not in the vocab of the model


In [23]:
similarities_static = test_util.get_similarities_of_models_static(model_static, test_case_dict_static)

  0%|          | 0/499 [00:00<?, ?it/s]

### TPPMI

In [24]:
%autoreload 2

from src.packages.TPPMI.ppmi_model import PPMIModel
from src.packages.TPPMI.tppmi_model import TPPMIModel
import src.test.util as test_util

In [25]:
sub_dirs = ["2000"] # each dir stores ppmi-data with the respective number of context words

# Collecting .npz files
ppmi_data_files = sorted([file for dir in sub_dirs
                          for file in glob(str(path_to_tppmi_model / dir / "*.npz"))])

# Collecting .pkl files
words_files = sorted([file for dir in sub_dirs
                      for file in glob(str(path_to_tppmi_model / dir / "*.pkl"))])

Split context-words from timestamped-vocabularies

In [26]:
context_words_files = [path for path in words_files if "context-words" in path]
ppmi_vocab_files = [path for path in words_files if "context-words" not in path]

In [27]:
for context_words_file in context_words_files:
    print(context_words_file)

../../data/ppmi-matrices/nyt-data/2000/context-words.pkl


In [28]:
# Get ppmi-matrices and vocab
ppmi_matrices= {}

for filenames in zip(ppmi_vocab_files, ppmi_data_files):
    ppmi_matrix = sp.load_npz(filenames[1])
    with open(filenames[0], "rb") as f:
        vocab = pickle.load(f)
    key = filenames[0].split("ppmi-")[2][0:4]
    ppmi_matrices[key] = {"ppmi_matrix" : ppmi_matrix, "vocab": vocab}

# Get common context-words
for context_words_file in context_words_files:
    with open(context_words_file, "rb") as f:
        context_words = pickle.load(f)

Create ppmi_model objects

In [29]:
ppmi_models = {key: PPMIModel.construct_from_data(ppmi_data["ppmi_matrix"], ppmi_data["vocab"], context_words, normalize=True) for key, ppmi_data in ppmi_matrices.items()}

In [30]:
tppmi_model = TPPMIModel(ppmi_models, dates="years", smooth=False)

Create test-dictionaries for all test cases

In [31]:
test_case_dict_tppmi = test_util.create_test_case_dict_tppmi(tppmi_model, test_cases)

19 Testcases are not in the vocab of the model


In [32]:
test_cases

array(['49ers-1990', '49ers-1995', 'agassi-1999', 'albright-1997',
       'albright-1998', 'albright-1999', 'albright-2000', 'athens-2004',
       'atlanta-1996', 'baker-1990', 'baker-1991', 'barak-1999',
       'barak-2000', 'barcelona-1992', 'bates-1991', 'beijing-2008',
       'benedict-2005', 'benedict-2006', 'benedict-2007', 'benedict-2008',
       'benedict-2009', 'benedict-2010', 'benedict-2011', 'benedict-2012',
       'bernanke-2006', 'bernanke-2007', 'bernanke-2008', 'bernanke-2009',
       'bernanke-2010', 'bernanke-2011', 'bernanke-2012', 'bernanke-2013',
       'berry-2002', 'biden-2008', 'biden-2009', 'biden-2010',
       'biden-2011', 'biden-2012', 'biden-2013', 'biden-2014',
       'biden-2015', 'biden-2016', 'blair-1997', 'blair-1998',
       'blair-1999', 'blair-2000', 'blair-2001', 'blair-2002',
       'blair-2003', 'blair-2004', 'blair-2005', 'blair-2006',
       'blasio-2014', 'blasio-2015', 'blasio-2016', 'bloomberg-2002',
       'bloomberg-2003', 'bloomberg-2004'

#### Calculate similarities

Calculate similarities for all testcases

In [33]:
similarities_tppmi = test_util.get_similarites_of_models_tppmi(tppmi_model, test_case_dict_tppmi)

  0%|          | 0/480 [00:00<?, ?it/s]

# Experiment

In [50]:
test_cases = test_data['truth'].unique()

## Categories of Testcases:

### Political Figures by Term
- **U.S. Presidents & Vice Presidents:**
Bush (1990-2007), Obama (2008-2016), Biden (2008-2016), Cheney (2000-2007), Gore (1992-1999), Clinton (1992-2012), Quayle (1990-1991)

- **International Leaders:**
Merkel (2005-2016), Sarkozy (2007-2011), Hollande (2012-2016), Netanyahu (1996-2016), Cameron (2010-2016), Blair (1997-2006), Major (1990-1996), Kohl (1990-1997), Chirac (1995-2006), Mitterrand (1990-1994), Putin (2000-2016), Modi (2014-2016)

### Sports Teams & Athletes by Year
- **NFL Teams:**
49ers (1990, 1995), Broncos (1998, 1999, 2016), Patriots (2002, 2004, 2005, 2015), Steelers (2006, 2009, 2011), Seahawks (2014), Rams (2000), Ravens (2001, 2013)

- **NBA Teams:**
Bulls (1991-1998), Lakers (2000-2002, 2009-2010), Heat (2006, 2012-2013), Spurs (2003, 2005, 2007, 2014), Rockets (1994-1995), Mavericks (2011), Cavaliers (2016), Knicks (1999), Pistons (1990, 2004)

- **Tennis Players:**
Sampras (1993-1998), Agassi (1999), Federer (2004-2009), Nadal (2008, 2010, 2013), Djokovic (2011, 2012, 2014-2015), Courier (1992), Edberg (1990-1991), Roddick (2003), Murray (2016)

### Natural Disasters and Epidemics
- **Natural Disasters:**
Katrina (2005), Sandy (2012), Ike (2008)
- **Epidemics:**
Cholera (1990), Plague (1994), SARS (2003), Ebola (2015), Zika (2016)

### Others
- **Special Events:**
Olympics (Barcelona-1992, Atlanta-1996, Sydney-2000, Athens-2004, Beijing-2008, London-2012, Rio-2016)

- **Prominent Personalities:**
Includes people like actors and directors (Spacey-2000, DiCaprio-2016)


In [210]:
test_data['category'].value_counts()

category
Other                            4601
International Leaders            2116
US-Politicians                   2015
NBA                               676
Tennis                            650
NFL                               506
Prominent Personalities           420
Natural Disasters & Epidemics      31
Special Events                     12
Name: count, dtype: int64

## Test differences in MRR

In [34]:
test_data["truth"].unique()

array(['49ers-1990', '49ers-1995', 'agassi-1999', 'albright-1997',
       'albright-1998', 'albright-1999', 'albright-2000', 'athens-2004',
       'atlanta-1996', 'baker-1990', 'baker-1991', 'barak-1999',
       'barak-2000', 'barcelona-1992', 'bates-1991', 'beijing-2008',
       'benedict-2005', 'benedict-2006', 'benedict-2007', 'benedict-2008',
       'benedict-2009', 'benedict-2010', 'benedict-2011', 'benedict-2012',
       'bernanke-2006', 'bernanke-2007', 'bernanke-2008', 'bernanke-2009',
       'bernanke-2010', 'bernanke-2011', 'bernanke-2012', 'bernanke-2013',
       'berry-2002', 'biden-2008', 'biden-2009', 'biden-2010',
       'biden-2011', 'biden-2012', 'biden-2013', 'biden-2014',
       'biden-2015', 'biden-2016', 'blair-1997', 'blair-1998',
       'blair-1999', 'blair-2000', 'blair-2001', 'blair-2002',
       'blair-2003', 'blair-2004', 'blair-2005', 'blair-2006',
       'blasio-2014', 'blasio-2015', 'blasio-2016', 'bloomberg-2002',
       'bloomberg-2003', 'bloomberg-2004'

In [54]:
sim_cade = similarities_cade[next(iter(similarities_cade))]
sim_tppmi = similarities_tppmi[next(iter(similarities_tppmi))]

In [55]:
print(next(iter(similarities_cade)))
sim_cade

49ers-1990


{'1990': [('49ers', 1.0),
  ('rams', 0.9142225384712219),
  ('broncos', 0.8876343369483948),
  ('everett', 0.8765201568603516),
  ('oilers', 0.8624967932701111),
  ('giants', 0.8569235801696777),
  ('vikings', 0.8563781380653381),
  ('eagles', 0.8512576222419739),
  ('quarterback', 0.8509493470191956),
  ('redskins', 0.8468084335327148)],
 '1991': [('falcons', 0.895034909248352),
  ('redskins', 0.8870956301689148),
  ('giants', 0.8732050657272339),
  ('eagles', 0.8424596190452576),
  ('49ers', 0.8326606750488281),
  ('lions', 0.8275255560874939),
  ('quarterback', 0.8203926682472229),
  ('jets', 0.8197599053382874),
  ('quarterbacks', 0.8186768889427185),
  ('bears', 0.8118192553520203)],
 '1992': [('redskins', 0.9050107002258301),
  ('49ers', 0.883254885673523),
  ('falcons', 0.8808400630950928),
  ('quarterback', 0.87618488073349),
  ('vikings', 0.8712279796600342),
  ('bengals', 0.8646988868713379),
  ('broncos', 0.8578092455863953),
  ('oilers', 0.8559005856513977),
  ('patriots', 

In [56]:
print(next(iter(similarities_tppmi)))
sim_tppmi

49ers-1990


{'1990': [('49ers', 1.0000000000000004),
  ('broncos', 0.4066686591692226),
  ('vikings', 0.38386446740599783),
  ('rams', 0.37491640895795897),
  ('giants', 0.37410898006308),
  ('quarterback', 0.3454107780757858),
  ('montana', 0.3449733650099112),
  ('touchdown', 0.32990901808816425),
  ('game', 0.3275822085159368),
  ('bowl', 0.3208675355969436)],
 '1991': [('giants', 0.4417569055026362),
  ('49ers', 0.37191559524540213),
  ('season', 0.3556187463286774),
  ('game', 0.3405850486240454),
  ('offense', 0.3302189832811052),
  ('eagles', 0.3150132513423995),
  ('handley', 0.3046157936157564),
  ('super', 0.3042464869215335),
  ('colts', 0.3035391197087715),
  ('yards', 0.30096316060433925)],
 '1992': [('giants', 0.3875728923555704),
  ('redskins', 0.3439689465831182),
  ('linebacker', 0.3341562550493373),
  ('jets', 0.33343852581210975),
  ('game', 0.33177856328246197),
  ('49ers', 0.3250851839980973),
  ('raiders', 0.3241870996753264),
  ('quarterback', 0.3225916460830906),
  ('bowl',

# Detailed Case Studies

Lets get the examples where TPPMI either outperformed the Cade-Model or the Cade-Model was way better at scoring this testcase

In [98]:
counter = 0
common_keys = set(similarities_cade.keys()) & set(similarities_tppmi.keys())
tppmi_wins = []
cade_wins = []
for key in common_keys:

    score_cade = test_util.calculate_mean_rank(key, similarities_cade[key], test_data)
    score_tppmi = test_util.calculate_mean_rank(key, similarities_tppmi[key], test_data)

    '''print(f"Key: {key}")
    print("TPPMI-Score")
    print(round(score_tppmi, 3))
    print("Cade-Score")
    print(round(score_cade, 3))''';

    if score_tppmi > score_cade:
        print("*********************")
        print("TPPMI has scored better at Key:")
        print(key)
        print("*********************")
        tppmi_wins.append(key)
    elif score_cade - score_tppmi > 0.5:
        print("*********************")
        print("Cade has scored way better at Key:")
        print(key)
        print("*********************")
        cade_wins.append(key)


*********************
TPPMI has scored better at Key:
chirac-2006
*********************
*********************
TPPMI has scored better at Key:
rice-2008
*********************
*********************
TPPMI has scored better at Key:
blair-1997
*********************
*********************
Cade has scored way better at Key:
putin-2004
*********************
*********************
Cade has scored way better at Key:
merkel-2011
*********************
*********************
TPPMI has scored better at Key:
shelton-2000
*********************
*********************
TPPMI has scored better at Key:
myers-2002
*********************
*********************
Cade has scored way better at Key:
merkel-2015
*********************
*********************
TPPMI has scored better at Key:
freeh-1998
*********************
*********************
TPPMI has scored better at Key:
cameron-2014
*********************
*********************
TPPMI has scored better at Key:
clinton-1999
*********************
*********************
TPPM

In [89]:
pprint(test_cases.tolist(), compact=True, width=120)

['49ers-1990', '49ers-1995', 'agassi-1999', 'albright-1997', 'albright-1998', 'albright-1999', 'albright-2000',
 'athens-2004', 'atlanta-1996', 'baker-1990', 'baker-1991', 'barak-1999', 'barak-2000', 'barcelona-1992', 'bates-1991',
 'beijing-2008', 'benedict-2005', 'benedict-2006', 'benedict-2007', 'benedict-2008', 'benedict-2009', 'benedict-2010',
 'benedict-2011', 'benedict-2012', 'bernanke-2006', 'bernanke-2007', 'bernanke-2008', 'bernanke-2009', 'bernanke-2010',
 'bernanke-2011', 'bernanke-2012', 'bernanke-2013', 'berry-2002', 'biden-2008', 'biden-2009', 'biden-2010',
 'biden-2011', 'biden-2012', 'biden-2013', 'biden-2014', 'biden-2015', 'biden-2016', 'blair-1997', 'blair-1998',
 'blair-1999', 'blair-2000', 'blair-2001', 'blair-2002', 'blair-2003', 'blair-2004', 'blair-2005', 'blair-2006',
 'blasio-2014', 'blasio-2015', 'blasio-2016', 'bloomberg-2002', 'bloomberg-2003', 'bloomberg-2004', 'bloomberg-2005',
 'bloomberg-2006', 'bloomberg-2007', 'bloomberg-2008', 'bloomberg-2009', 'blo

Here are the examples where Cade was significantly better (+0.5 score or higher)

In [81]:
print(f"Cade decisive wins: {len(cade_wins)}")
print(cade_wins)

Cade decisive wins: 29
['putin-2004', 'merkel-2011', 'merkel-2015', 'sharon-2002', 'francis-2015', 'putin-2015', 'netanyahu-2014', 'merkel-2016', 'sharon-2005', 'yeltsin-1992', 'yeltsin-1991', 'rabin-1994', 'giuliani-1999', 'merkel-2014', 'sharon-2003', 'sandy-2012', 'kohl-1993', 'powell-2004', 'kohl-1994', 'kohl-1992', 'sharon-2001', 'hollande-2015', 'yeltsin-1998', 'putin-2007', 'putin-2016', 'yeltsin-1995', 'putin-2014', 'ike-2008', 'kohl-1991']


Here are the examples where TPPMI scored better on a testcase than the Cade-Model

In [82]:
print(f"TPPMI wins: {len(tppmi_wins)}")
print(tppmi_wins)

TPPMI wins: 78
['chirac-2006', 'rice-2008', 'blair-1997', 'shelton-2000', 'myers-2002', 'freeh-1998', 'cameron-2014', 'clinton-1999', 'greenspan-1993', 'murray-2016', 'roberts-2012', 'cavaliers-2016', 'djokovic-2014', 'myers-2004', 'zika-2016', 'dempsey-2013', 'obama-2013', 'bernanke-2012', 'mueller-2009', 'greenspan-2002', 'clinton-1995', 'rehnquist-2001', 'mueller-2007', 'bush-2007', 'greenspan-2003', 'blair-2006', 'powell-1990', 'rehnquist-2000', 'bush-2002', 'clinton-1994', 'singh-2013', 'freeh-1999', 'greenspan-2001', 'cameron-2016', 'roberts-2013', 'shelton-1998', 'bush-2006', 'biden-2016', 'rehnquist-1994', 'broncos-2016', 'roberts-2008', 'dempsey-2011', 'biden-2011', 'brennan-2013', 'rio-2016', 'blair-2000', 'clinton-2011', 'tenet-1999', 'hayden-2008', 'bush-2005', 'hayden-2007', 'clinton-2012', 'clinton-1996', 'blair-1999', 'mueller-2005', 'rehnquist-1999', 'likud-1991', 'pace-2006', 'webster-1990', 'biden-2010', 'dempsey-2014', 'rehnquist-1990', 'biden-2014', 'blasio-2016', '

# Samples

In [113]:
def print_labels_and_get_test_df(key: str, print_labels=False) -> pd.DataFrame:
    sorted_data = sorted(test_data[test_data.truth == key].equivalent.tolist(), key=lambda x: int(x.split('-')[1]))

    df = pd.DataFrame(sorted_data, columns=['combined'])
    df[['name', 'year']] = df['combined'].str.split('-', expand=True)
    df = df.drop("combined", axis=1)
    if print_labels:
        print(test_key)
        pprint(sorted_data, compact=True, width=100)
    return df

## #1 Sample from Cade-Winning: putin-2004

The embedding for "putin-2014" should ideally capture the significant facets of Vladimir Putin’s role and political actions in the year 2014. This period marked heightened international attention on Putin due to Russia's involvement in the Ukraine crisis, specifically the annexation of Crimea. The embedding should reflect his interactions with global leaders, Russia's diplomatic stance against Western sanctions, and his image both within Russia and on the world stage.

In [196]:
test_key = "putin-2004"

In [197]:
df_test = print_labels_and_get_test_df(test_key, print_labels=True)

putin-2004
['yeltsin-1991', 'yeltsin-1992', 'yeltsin-1993', 'yeltsin-1994', 'yeltsin-1995', 'yeltsin-1996',
 'yeltsin-1997', 'yeltsin-1998', 'yeltsin-1999', 'putin-2000', 'putin-2001', 'putin-2002',
 'putin-2003', 'putin-2005', 'putin-2006', 'putin-2007', 'medvedev-2008', 'medvedev-2009',
 'medvedev-2010', 'medvedev-2011', 'putin-2012', 'putin-2013', 'putin-2014', 'putin-2015',
 'putin-2016']


In [198]:
print("TPPMIModel-2000")
print(test_util.get_quick_mrr(test_key, similarities_tppmi, df_test))
print("Cade")
print(test_util.get_quick_mrr(test_key, similarities_cade, df_test))

TPPMIModel-2000
0.151
Cade
0.679


In [199]:
similarities_tppmi[test_key]

{'1990': [('gorbachev', 0.333118270354044),
  ('party', 0.3026918859363163),
  ('opposition', 0.29728965656302747),
  ('political', 0.2958140730420698),
  ('economic', 0.2903159345301721),
  ('parliament', 0.2878450324500907),
  ('gorbachevs', 0.27889596474057954),
  ('leadership', 0.27294875940316526),
  ('soviet', 0.27007387651762194),
  ('communist', 0.2653839559896156)],
 '1991': [('gorbachev', 0.32055017170894784),
  ('party', 0.311629438227929),
  ('yeltsin', 0.29156982789725044),
  ('republics', 0.28702554477397396),
  ('mikhail', 0.28593893101268913),
  ('union', 0.2761244239770549),
  ('political', 0.27462990655844827),
  ('soviet', 0.2738134088179123),
  ('democratic', 0.2672451543059819),
  ('gorbachevs', 0.267055079347428)],
 '1992': [('election', 0.280994305397808),
  ('minister', 0.27517686913749007),
  ('political', 0.2710864794741856),
  ('communist', 0.2686040941266556),
  ('democrats', 0.26334047852886466),
  ('foreign', 0.2611706691588309),
  ('party', 0.259926368094

In [121]:
similarities_cade[test_key]

{'1990': [('yeltsin', 0.8153406977653503),
  ('gorbachev', 0.8152757883071899),
  ('gorbachevs', 0.8062798380851746),
  ('kohl', 0.7713931202888489),
  ('mitterrand', 0.758574903011322),
  ('dictator', 0.7312790155410767),
  ('lithuania', 0.7293031811714172),
  ('independence', 0.7255465388298035),
  ('yeltsins', 0.7082157731056213),
  ('bushs', 0.7026031613349915)],
 '1991': [('yeltsin', 0.8703688979148865),
  ('yeltsins', 0.8507915139198303),
  ('gorbachev', 0.8364452719688416),
  ('gorbachevs', 0.7903742790222168),
  ('milosevic', 0.7736449837684631),
  ('showdown', 0.7489731311798096),
  ('mitterrand', 0.7393612265586853),
  ('singh', 0.7318919897079468),
  ('hosni', 0.7121748924255371),
  ('mubarak', 0.7006976008415222)],
 '1992': [('milosevic', 0.8532339930534363),
  ('yeltsins', 0.8380856513977051),
  ('yeltsin', 0.8283174633979797),
  ('slobodan', 0.7360499501228333),
  ('mubarak', 0.7197384238243103),
  ('likud', 0.7102648019790649),
  ('shamir', 0.6914985775947571),
  ('gorba

## #2 Sample from Cade-Winning: Merkel-2016

The embedding for "merkel-2016" should ideally represent the semantic and contextual associations of Angela Merkel during the year 2016, capturing her role and activities as the Chancellor of Germany. It should reflect her involvement in key international crises, interactions with global leaders, and influence on significant policy decisions, particularly in the context of the European migrant crisis and Brexit discussions.

In [190]:
test_key = "merkel-2016"

In [191]:
df_test = print_labels_and_get_test_df(test_key, print_labels=True)

merkel-2016
['kohl-1990', 'kohl-1991', 'kohl-1992', 'kohl-1993', 'kohl-1994', 'kohl-1995', 'kohl-1996',
 'kohl-1997', 'merkel-2005', 'merkel-2006', 'merkel-2007', 'merkel-2008', 'merkel-2009',
 'merkel-2010', 'merkel-2011', 'merkel-2012', 'merkel-2013', 'merkel-2014', 'merkel-2015']


In [192]:
print("TPPMIModel-2000")
print(test_util.get_quick_mrr(test_key, similarities_tppmi, df_test))
print("Cade")
print(test_util.get_quick_mrr(test_key, similarities_cade, df_test))

TPPMIModel-2000
0.083
Cade
0.518


In [129]:
similarities_tppmi[test_key]

{'1990': [('unification', 0.19724340986832833),
  ('helmut', 0.1932693475647685),
  ('hitler', 0.19103854662218211),
  ('germany', 0.18674868251784385),
  ('economic', 0.18629665029202708),
  ('kohl', 0.18605174867891108),
  ('soviet', 0.18070216305592451),
  ('uncertainty', 0.17971211130113895),
  ('nato', 0.17831757441477775),
  ('external', 0.17478889872307465)],
 '1991': [('unification', 0.20023475160009596),
  ('soviet', 0.18885037349517797),
  ('warsaw', 0.18022491162977633),
  ('country', 0.1764794411583666),
  ('union', 0.17595879989339588),
  ('nations', 0.17429795313616783),
  ('utopia', 0.17400075153065978),
  ('sydney', 0.17352998153185384),
  ('presidency', 0.17156198366322994),
  ('worsen', 0.16996867483003525)],
 '1992': [('germany', 0.19403983289173588),
  ('electorate', 0.19336235340308527),
  ('repression', 0.19108893416360542),
  ('helmut', 0.17914998448245803),
  ('minister', 0.1783891939526748),
  ('currency', 0.1765533961969655),
  ('widening', 0.17433533036184173

In [130]:
similarities_cade[test_key]

{'1990': [('kohl', 0.744658350944519),
  ('helmut', 0.7280738353729248),
  ('unification', 0.7086880207061768),
  ('mitterrand', 0.707364022731781),
  ('warsaw', 0.6832961440086365),
  ('thatcher', 0.6830325126647949),
  ('reunited', 0.6808640956878662),
  ('reunification', 0.6754075288772583),
  ('estonia', 0.6716198921203613),
  ('chancellor', 0.6686394214630127)],
 '1991': [('kohl', 0.7676426768302917),
  ('helmut', 0.7221391797065735),
  ('latvia', 0.710848331451416),
  ('kazakhstan', 0.6997746229171753),
  ('milosevic', 0.677112877368927),
  ('bonn', 0.6699168086051941),
  ('aleksandr', 0.6582573652267456),
  ('mitterrand', 0.6502012014389038),
  ('russia', 0.6452451348304749),
  ('yugoslavia', 0.6452138423919678)],
 '1992': [('kohl', 0.7883138656616211),
  ('helmut', 0.7333889603614807),
  ('yeltsins', 0.7055099010467529),
  ('yeltsin', 0.6912229657173157),
  ('belarus', 0.6697692275047302),
  ('russia', 0.6690551042556763),
  ('mitterrand', 0.6251556873321533),
  ('shamir', 0.61

## #1 Sample from TPPMI-Winning: djokovic-2014

The embedding for "Djokovic-2014" should accurately represent the career highlights and key moments of Novak Djokovic in the year 2014, focusing on his achievements in tennis. This includes his performance in major tournaments, particularly his victory at Wimbledon and his final appearances in other Grand Slam events.

In [188]:
test_key = "djokovic-2014"

In [189]:
df_test = print_labels_and_get_test_df(test_key, print_labels=True)

djokovic-2014
['edberg-1990', 'edberg-1991', 'courier-1992', 'sampras-1993', 'sampras-1994', 'sampras-1995',
 'sampras-1996', 'sampras-1997', 'sampras-1998', 'agassi-1999', 'hewitt-2001', 'hewitt-2002',
 'roddick-2003', 'federer-2004', 'federer-2005', 'federer-2006', 'federer-2007', 'nadal-2008',
 'federer-2009', 'nadal-2010', 'djokovic-2011', 'djokovic-2012', 'nadal-2013', 'djokovic-2015',
 'murray-2016']


In [179]:
print("TPPMIModel-2000")
print(test_util.get_quick_mrr(test_key, similarities_tppmi, df_test))
print("Cade")
print(test_util.get_quick_mrr(test_key, similarities_cade, df_test))

TPPMIModel-2000
0.292
Cade
0.257


In [180]:
similarities_tppmi[test_key]

{'1990': [('graf', 0.21042668113214288),
  ('soccer', 0.20433505560254284),
  ('final', 0.2004959065270123),
  ('semifinal', 0.19323493053827998),
  ('19', 0.19301463109524206),
  ('becker', 0.1898535842280865),
  ('game', 0.18882212494645834),
  ('victory', 0.18864112972729483),
  ('defeating', 0.18812476598919242),
  ('player', 0.18622134286596506)],
 '1991': [('wimbledon', 0.20878918165393195),
  ('points', 0.20571157193368575),
  ('semifinal', 0.20568558569809028),
  ('edberg', 0.20505623152596952),
  ('championship', 0.19719131939397289),
  ('stefan', 0.19626167367000505),
  ('slam', 0.19153985561001205),
  ('game', 0.19118790945979106),
  ('basketball', 0.1899660755698871),
  ('ncaa', 0.18595075821892504)],
 '1992': [('wimbledon', 0.23394519507509873),
  ('undefeated', 0.20843220311559066),
  ('raiders', 0.207553459925577),
  ('seeded', 0.20099306237450165),
  ('game', 0.19765486109009775),
  ('season', 0.1966337085610324),
  ('edberg', 0.19248971550923705),
  ('lacrosse', 0.1890

In [181]:
similarities_cade[test_key]

{'1990': [('becker', 0.8629920482635498),
  ('lendl', 0.8590437769889832),
  ('navratilova', 0.8252697587013245),
  ('agassi', 0.8171017169952393),
  ('edberg', 0.8088446855545044),
  ('martina', 0.8045077919960022),
  ('graf', 0.798007607460022),
  ('quarterfinals', 0.7950503826141357),
  ('wimbledon', 0.7732568383216858),
  ('stefan', 0.7621898651123047)],
 '1991': [('stefan', 0.8551492691040039),
  ('edberg', 0.819786787033081),
  ('seles', 0.8122759461402893),
  ('graf', 0.7946069240570068),
  ('quarterfinals', 0.7887965440750122),
  ('sampras', 0.7873258590698242),
  ('courier', 0.7592945694923401),
  ('agassi', 0.750734806060791),
  ('seeded', 0.7489088177680969),
  ('sanchez', 0.7462663650512695)],
 '1992': [('stefan', 0.829885721206665),
  ('sampras', 0.8264800906181335),
  ('graf', 0.8065250515937805),
  ('edberg', 0.7954472899436951),
  ('courier', 0.7927203178405762),
  ('agassi', 0.7881489396095276),
  ('becker', 0.7809476852416992),
  ('quarterfinals', 0.741105318069458),


## #2 Sample from TPPMI-Winning: biden-2014

The embedding for "biden-2014" should ideally represent the semantic and contextual associations of Joe Biden during the year 2014, capturing his role and activities as the Vice President of the United States under the Obama administration. It should reflect his involvement in key political events, interactions with major political figures, and influence on significant policy decisions

In [183]:
test_key = "biden-2014"

In [184]:
df_test = print_labels_and_get_test_df(test_key, print_labels=True)

biden-2014
['quayle-1990', 'quayle-1991', 'gore-1992', 'gore-1993', 'gore-1994', 'gore-1995', 'gore-1996',
 'gore-1997', 'gore-1998', 'gore-1999', 'cheney-2000', 'cheney-2001', 'cheney-2002', 'cheney-2003',
 'cheney-2004', 'cheney-2005', 'cheney-2006', 'cheney-2007', 'biden-2008', 'biden-2009',
 'biden-2010', 'biden-2011', 'biden-2012', 'biden-2013', 'biden-2015', 'biden-2016']


In [185]:
print("TPPMIModel-2000")
print(test_util.get_quick_mrr(test_key, similarities_tppmi, df_test))
print("Cade")
print(test_util.get_quick_mrr(test_key, similarities_cade, df_test))

TPPMIModel-2000
0.24
Cade
0.225


In [186]:
similarities_tppmi[test_key]

{'1990': [('peggy', 0.20853075717865663),
  ('mr', 0.19133396587992824),
  ('john', 0.18871026687298703),
  ('crowley', 0.188473562488638),
  ('handled', 0.18553860387465218),
  ('nomination', 0.18178371330843884),
  ('donald', 0.18168228014973026),
  ('whitehead', 0.17926917982868368),
  ('appointed', 0.17764378588047813),
  ('gorbachev', 0.1774954822923953)],
 '1991': [('mr', 0.21204091982267795),
  ('f', 0.21053664736108837),
  ('president', 0.20484284012713175),
  ('said', 0.2044302805497239),
  ('bushs', 0.2038303578753211),
  ('robert', 0.2022154070659266),
  ('e', 0.19380780631894076),
  ('democratic', 0.19334598517418936),
  ('rockies', 0.1893368492846603),
  ('bush', 0.18849317578226052)],
 '1992': [('president', 0.24056644238747635),
  ('bushs', 0.21569799853046615),
  ('bush', 0.20283835209651363),
  ('headed', 0.18549875658913248),
  ('gov', 0.18093638533750056),
  ('governor', 0.17977234493643132),
  ('planning', 0.179023249636807),
  ('partys', 0.17857960367317144),
  ('m

In [187]:
similarities_cade[test_key]

{'1990': [('f', 0.7877159714698792),
  ('sununu', 0.7508372664451599),
  ('koch', 0.7403224110603333),
  ('lyndon', 0.700463593006134),
  ('daniels', 0.6889458298683167),
  ('borough', 0.6816033720970154),
  ('quayle', 0.6803681254386902),
  ('moynihan', 0.6776978373527527),
  ('kennedy', 0.677545964717865),
  ('vallone', 0.6765803098678589)],
 '1991': [('truman', 0.7645207643508911),
  ('giuliani', 0.7562885284423828),
  ('f', 0.7351701259613037),
  ('nixon', 0.7158361077308655),
  ('vallone', 0.7097360491752625),
  ('mccall', 0.7078900933265686),
  ('w', 0.7070724964141846),
  ('quayle', 0.7046210765838623),
  ('koch', 0.6987043023109436),
  ('rudolph', 0.6836525201797485)],
 '1992': [('giuliani', 0.7593206167221069),
  ('messinger', 0.7431172728538513),
  ('stein', 0.7322641611099243),
  ('predecessor', 0.7199902534484863),
  ('moynihan', 0.718794047832489),
  ('truman', 0.7170758247375488),
  ('reagans', 0.7143393158912659),
  ('w', 0.7117213010787964),
  ('kennedy', 0.708359003067